# MNIST classification: how to feed the data to the model
1- MNIST dataset in memory  
2- Transform the numpy array as images  
3- Create and save the JPEG images on the Cloud Storage  
4- Dataset to read numpy array in memory  
5- Create TFRecords to store numpy array  
6- Dataset to read TFRecord with numpy array  
7- Create TFRecords to store JPEG images  
8- Dataset to read TFRecord with JPEG images  

## Install packages on Google  Cloud Datalab (locally use conda env)

### Select in the Python3 Kernel:
In the menu bar the of 'Kernel', select   
**python3**
### Install needed packages
copy the command below in a Google Cloud Datalab cell  
**!pip install tensorflow==1.12**
### Restart the Kernel 
this is to take into account the new installed packages. Click in the menu bar on:  
**Reset Session**

## Include paths to our functions

In [1]:
import sys
import os
import pathlib

workingdir=os.getcwd()
print(workingdir)
d=[d for d in os.listdir(workingdir)]
n=0
while not set(['notebook']).issubset(set(d)):
   workingdir=str(pathlib.Path(workingdir).parents[0])
   print(workingdir)
   d=[d for d in os.listdir(str(workingdir))]
   n+=1
   if n>5:
       break
sys.path.insert(0, workingdir)
os.chdir(workingdir)

/Users/tarrade/Desktop/Work/Data_Science/Tutorials_Codes/Python/proj_DL_models_and_pipelines_with_GCP/notebook
/Users/tarrade/Desktop/Work/Data_Science/Tutorials_Codes/Python/proj_DL_models_and_pipelines_with_GCP


## Setup librairies import and plots style

### Import librairies

In [2]:
import tensorflow as tf
import numpy as np
import matplotlib.pyplot as plt
import time
import gzip
import sys
import shutil
import _pickle as cPickle
from PIL import Image
import glob as glob

In [3]:
print(tf.__version__)
print(tf.keras.__version__)

1.12.0
2.1.6-tf


### Import our utils functions

In [4]:
import src.utils.mnist_utils as mnist_utils
import src.utils.tensorflow_helper as tensorflow_helper
import src.model_mnist_v1.trainer.model as mnist_v1

In [5]:
import importlib
importlib.reload(mnist_utils)
importlib.reload(mnist_v1)
importlib.reload(tensorflow_helper);# to reload the function and mask the output

## Input Data
### Load the data

In [6]:
# load the data: path is relative to the python path!
(x_train, y_train), (x_test, y_test) = mnist_utils.load_data(path='data/mnist/raw/mnist.pkl.gz')

### Basics checks

In [7]:
# check data shape (training)
x_train.shape

(60000, 28, 28)

In [8]:
# check data shape (train)
x_test.shape

(10000, 28, 28)

In [9]:
x_train.dtype, x_test.dtype

(dtype('uint8'), dtype('uint8'))

In [10]:
np.max(x_train), np.min(x_train), np.max(x_test), np.min(x_test) 

(255, 0, 255, 0)

## Save Numpy array as JPEG as images

In [11]:
path_train_images='data/mnist/images_train/'
path_test_images='data/mnist/images_test/'

In [12]:
if not os.path.exists(path_train_images):
    os.makedirs(path_train_images)

In [13]:
if not os.path.exists(path_test_images):
    os.makedirs(path_test_images)

In [14]:
for i, im_array in enumerate(x_train):
    im = Image.fromarray(im_array)
    im.save(path_train_images+'image_train_'+str(i).zfill(5)+'_label_'+str(y_train[i]).zfill(2)+'.jpeg')

In [15]:
for i, im_array in enumerate(x_test):
    im = Image.fromarray(im_array)
    im.save(path_test_images+'image_test_'+str(i).zfill(5)+'_label_'+str(y_test[i]).zfill(2)+'.jpeg')

## Save JPEG images on GCP

In [16]:
GCS_BUCKET = 'gs://ml-productive-pipeline-53122' 
PROJECT = 'ml-productive-pipeline-53122'
REGION = 'europe-west1'
LOCAL_DATA_TEST = path_test_images
LOCAL_DATA_TRAIN = path_train_images

In [17]:
os.environ['GCS_BUCKET'] = GCS_BUCKET
os.environ['PROJECT'] = PROJECT
os.environ['REGION'] = REGION
os.environ['LOCAL_DATA_TEST'] = LOCAL_DATA_TEST
os.environ['LOCAL_DATA_TRAIN'] = LOCAL_DATA_TRAIN

In [18]:
!gsutil ls $GCS_BUCKET/mnist/raw

gs://ml-productive-pipeline-53122/mnist/raw/test/
gs://ml-productive-pipeline-53122/mnist/raw/train/


In [19]:
!gsutil -m cp -R $LOCAL_DATA_TRAIN/ $GCS_BUCKET/mnist/image/train

Copying file://data/mnist/images_train//image_train_32393_label_05.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_12203_label_09.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_29253_label_05.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_01391_label_02.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_04578_label_08.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_06650_label_07.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_25019_label_09.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_09968_label_09.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_42631_label_05.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_34964_label_02.jpeg [Content-Type=image

Copying file://data/mnist/images_train//image_train_42439_label_02.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_19139_label_01.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_57372_label_07.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_49537_label_02.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_28636_label_09.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_48756_label_08.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_21410_label_06.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_06521_label_01.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_59480_label_03.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_29845_label_05.jpeg [Content-Type=image

Copying file://data/mnist/images_train//image_train_30665_label_00.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_52438_label_00.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_46107_label_01.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_31541_label_04.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_56099_label_01.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_52411_label_01.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_17768_label_08.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_01156_label_07.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_03257_label_09.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_59536_label_00.jpeg [Content-Type=image

Copying file://data/mnist/images_train//image_train_20864_label_09.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_24702_label_07.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_50231_label_08.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_43871_label_02.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_48806_label_03.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_16028_label_05.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_15148_label_01.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_58333_label_03.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_39177_label_06.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_11897_label_09.jpeg [Content-Type=image

Copying file://data/mnist/images_train//image_train_35546_label_04.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_12527_label_03.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_14810_label_03.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_49027_label_00.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_07997_label_06.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_07329_label_08.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_11452_label_09.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_38284_label_04.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_13616_label_09.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_13753_label_07.jpeg [Content-Type=image

...

Copying file://data/mnist/images_train//image_train_38429_label_00.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_02351_label_09.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_02344_label_07.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_00045_label_09.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_38579_label_00.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_12921_label_07.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_02378_label_08.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_16192_label_00.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_28262_label_09.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_13747_label_05.jpeg [Content-Type=image

Copying file://data/mnist/images_train//image_train_48149_label_08.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_16419_label_07.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_59576_label_05.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_16560_label_06.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_06587_label_07.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_29588_label_04.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_38662_label_00.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_02063_label_08.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_59426_label_05.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_16430_label_06.jpeg [Content-Type=image

Copying file://data/mnist/images_train//image_train_29805_label_00.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_05291_label_07.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_00444_label_02.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_15333_label_08.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_01619_label_07.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_49562_label_09.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_05428_label_01.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_29402_label_08.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_13203_label_00.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_00906_label_04.jpeg [Content-Type=image

Copying file://data/mnist/images_train//image_train_29928_label_06.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_49931_label_06.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_00569_label_04.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_01734_label_01.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_14106_label_05.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_16482_label_02.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_28637_label_05.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_13990_label_08.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_03827_label_09.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_03977_label_09.jpeg [Content-Type=image

Copying file://data/mnist/images_train//image_train_42594_label_07.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_30657_label_07.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_09073_label_05.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_30712_label_09.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_51951_label_04.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_57466_label_04.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_52831_label_00.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_08497_label_06.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_18459_label_06.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_train//image_train_08482_label_08.jpeg [Content-Type=image

In [20]:
!gsutil -m cp -R $LOCAL_DATA_TEST/ $GCS_BUCKET/mnist/image/test

Copying file://data/mnist/images_test//image_test_06836_label_02.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_00843_label_04.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_04189_label_02.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_00528_label_03.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_05148_label_01.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_09662_label_03.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_05902_label_01.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_05469_label_06.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_05031_label_00.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_04481_label_04.jpeg [Content-Type=image/jpeg]...
Copying fi

Copying file://data/mnist/images_test//image_test_02297_label_08.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_04467_label_07.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_00988_label_01.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_03775_label_02.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_09576_label_07.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_08277_label_03.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_07018_label_05.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_04178_label_01.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_09919_label_07.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_09875_label_08.jpeg [Content-Type=image/jpeg]...
Copying fi

Copying file://data/mnist/images_test//image_test_03364_label_08.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_01120_label_08.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_02055_label_02.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_03208_label_07.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_09022_label_03.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_05721_label_00.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_00764_label_02.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_03054_label_07.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_03068_label_08.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_03041_label_09.jpeg [Content-Type=image/jpeg]...
Copying fi

Copying file://data/mnist/images_test//image_test_04744_label_08.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_03290_label_03.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_00419_label_01.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_06119_label_07.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_02591_label_07.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_06130_label_06.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_08961_label_04.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_03025_label_04.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_09712_label_08.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_08948_label_05.jpeg [Content-Type=image/jpeg]...
Copying fi

Copying file://data/mnist/images_test//image_test_09132_label_05.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_07790_label_01.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_02145_label_04.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_07079_label_07.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_08722_label_08.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_07050_label_06.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_02534_label_03.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_00609_label_02.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_03755_label_09.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_04438_label_04.jpeg [Content-Type=image/jpeg]...
Copying fi

...

Copying file://data/mnist/images_test//image_test_07435_label_03.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_01510_label_05.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_01031_label_02.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_07448_label_05.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_02548_label_09.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_01956_label_04.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_02561_label_08.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_02028_label_07.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_00649_label_07.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_08777_label_03.jpeg [Content-Type=image/jpeg]...
Copying fi

Copying file://data/mnist/images_test//image_test_04219_label_05.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_04745_label_04.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_07625_label_00.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_08858_label_00.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_08581_label_03.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_02782_label_06.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_01845_label_03.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_00884_label_00.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_04282_label_00.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_04407_label_09.jpeg [Content-Type=image/jpeg]...
Copying fi

Copying file://data/mnist/images_test//image_test_05654_label_07.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_04695_label_04.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_01040_label_01.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_02799_label_03.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_06993_label_02.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_09697_label_03.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_05434_label_08.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_05421_label_06.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_00926_label_02.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_03846_label_06.jpeg [Content-Type=image/jpeg]...
Copying fi

Copying file://data/mnist/images_test//image_test_00455_label_01.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_05802_label_05.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_07308_label_02.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_04986_label_08.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_03069_label_04.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_03610_label_04.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_00620_label_00.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_08737_label_05.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_07833_label_04.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_04568_label_07.jpeg [Content-Type=image/jpeg]...
Copying fi

Copying file://data/mnist/images_test//image_test_07248_label_03.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_02091_label_07.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_01896_label_05.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_04731_label_08.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_01618_label_05.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_04648_label_09.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_06150_label_08.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_08292_label_02.jpeg [Content-Type=image/jpeg]...
Copying file://data/mnist/images_test//image_test_08969_label_02.jpeg [Content-Type=image/jpeg]...
\ [10.0k/10.0k files][  5.4 MiB/  5.4 MiB] 100% Done  26.0 KiB/s ETA 00:00:00   
Operation completed over 10.

## Set parameters

In [21]:
tf.logging.set_verbosity(tf.logging.INFO)

In [22]:
# number of classes
NUM_CLASSES =10

# dimension of the input data
DIM_INPUT = 784

# number of epoch to train our model
EPOCHS = 2

# size of our mini batch
BATCH_SIZE = 128

# shuffle buffer size
SHUFFLE_BUFFER_SIZE = 10 * BATCH_SIZE

# prefetch buffer size
PREFETCH_BUFFER_SIZE = tf.contrib.data.AUTOTUNE

# number of paralell calls
NUM_PARALELL_CALL = 4

# model version
MODEL='v1'

## Defined flags

In [23]:
tensorflow_helper.del_all_flags(tf.flags.FLAGS)

In [24]:
# just for jupyter notebook and avoir : "UnrecognizedFlagError: Unknown command line flag 'f'"
tf.app.flags.DEFINE_string('f', '', 'kernel') 

# path to store the model and input for Tensorboard
tf.app.flags.DEFINE_string('model_dir_keras', './results/Models/Mnist/tf_1_12/keras/'+MODEL+'/ckpt/', 'Dir to save a model and checkpoints with keras')
tf.app.flags.DEFINE_string('tensorboard_dir_keras', './results/Models/Mnist/tf_1_12/keras/'+MODEL+'/logs/', 'Dir to save logs for TensorBoard with keras')

# parameters for the input dataset and train the model
tf.app.flags.DEFINE_integer('epoch', EPOCHS, 'number of epoch')
tf.app.flags.DEFINE_integer('step_per_epoch', len(x_train) // BATCH_SIZE, 'number of step per epoch')
tf.app.flags.DEFINE_integer('batch_size', BATCH_SIZE, 'Batch size')
tf.app.flags.DEFINE_integer('shuffle_buffer_size', SHUFFLE_BUFFER_SIZE , 'Shuffle buffer size')
tf.app.flags.DEFINE_integer('prefetch_buffer_size', PREFETCH_BUFFER_SIZE, 'Prefetch buffer size')
tf.app.flags.DEFINE_integer('num_parallel_calls', NUM_PARALELL_CALL, 'Number of paralell calls')

# parameters for the model
tf.app.flags.DEFINE_integer('num_classes', NUM_CLASSES, 'number of classes in our model')
tf.app.flags.DEFINE_integer('dim_input', DIM_INPUT, 'dimension of the input data for our model')

FLAGS = tf.app.flags.FLAGS

## Dataset to preprocess and feed data in our model 
Use tf.data.dataset it will prepare mini batches of data, reshuffle the data, parallelized the pre-processing the data. 

https://www.tensorflow.org/guide/performance/datasets  
To summarize, one good order for the different transformations is:
- create the dataset
- shuffle (with a big enough buffer size)  
https://stackoverflow.com/questions/46444018/meaning-of-buffer-size-in-dataset-map-dataset-prefetch-and-dataset-shuffle)
- repeat
- map with the actual work (preprocessing, augmentation…) using multiple parallel calls
- batch
- prefetch

ModeKeys:  
https://www.tensorflow.org/api_docs/python/tf/estimator/ModeKeys  
- EVAL
- PREDICT
- TRAIN

### Printing the number relater to the number of events (epoch, batch size, ...)

In [25]:
def print_summary_input(data, step='training'):
    print('Summary for the {} dataset:'.format(step))
    if step=='training':
        print('  - number of epoch            :', FLAGS.epoch)
        print('  - number of events per epoch :', len(data))
        print('  - batch size                 :', FLAGS.batch_size)
        print('  - number of step per epoch   :', FLAGS.step_per_epoch)
        print('  - total number of steps      :', FLAGS.epoch * FLAGS.step_per_epoch)
    else:
        print('  - number of epoch            :', 1)
        print('  - number of events per epoch :', len(data))
        print('  - batch size                 :', None)
        print('  - number of step per epoch   :', 1)
        print('  - total number of steps      :', 1) 

In [26]:
print_summary_input(x_train)

Summary for the training dataset:
  - number of epoch            : 2
  - number of events per epoch : 60000
  - batch size                 : 128
  - number of step per epoch   : 468
  - total number of steps      : 936


In [27]:
print_summary_input(x_test)

Summary for the training dataset:
  - number of epoch            : 2
  - number of events per epoch : 10000
  - batch size                 : 128
  - number of step per epoch   : 468
  - total number of steps      : 936


### Dataset using numpy array to preprocess and feed data in our model 

#### Creating "Graph" for the datasets

In [28]:
training_dataset = mnist_v1.input_mnist_array_dataset_fn(x_train, 
                                                         y_train, 
                                                         FLAGS,
                                                         mode=tf.estimator.ModeKeys.TRAIN, 
                                                         batch_size=FLAGS.batch_size)

INFO:tensorflow:input_dataset_fn: TRAIN, train


In [29]:
testing_dataset = mnist_v1.input_mnist_array_dataset_fn(x_test, 
                                                        y_test,
                                                        FLAGS,
                                                        mode=tf.estimator.ModeKeys.EVAL, 
                                                        batch_size=len(x_test))

INFO:tensorflow:input_dataset_fn: EVAL, eval


In [30]:
training_dataset, testing_dataset

(<PrefetchDataset shapes: ((128, 784), (128, 10)), types: (tf.float32, tf.float32)>,
 <PrefetchDataset shapes: ((10000, 784), (10000, 10)), types: (tf.float32, tf.float32)>)

#### Executing the "Graph for the datasets" for training

In [31]:
# create an iterator
iterator = training_dataset.make_one_shot_iterator()

# next_element
features, labels = iterator.get_next()

In [32]:
n=0

n_iter=12
with tf.Session() as sess:
    while True:
        try:
            start_time = time.clock()
            x,y = sess.run([features, labels])
            print('iteration n:', n, 'execution time:', time.clock() - start_time, 'seconds')
            print(x.shape)
            print(y.shape)
            print('first label of the batch',np.argmax(y[0]),'\n')
            n+=1
            if n>=n_iter:
                print('number of iteration reached')
                break
        except tf.errors.OutOfRangeError:
            print('tf.errors.OutOfRangeError')
            break

iteration n: 0 execution time: 2.139353 seconds
(128, 784)
(128, 10)
first label of the batch 9 

iteration n: 1 execution time: 0.021308000000004768 seconds
(128, 784)
(128, 10)
first label of the batch 2 

iteration n: 2 execution time: 0.030722999999994727 seconds
(128, 784)
(128, 10)
first label of the batch 6 

iteration n: 3 execution time: 0.026539000000013857 seconds
(128, 784)
(128, 10)
first label of the batch 1 

iteration n: 4 execution time: 0.03009300000002213 seconds
(128, 784)
(128, 10)
first label of the batch 5 

iteration n: 5 execution time: 0.03334099999997875 seconds
(128, 784)
(128, 10)
first label of the batch 1 

iteration n: 6 execution time: 0.02966899999998418 seconds
(128, 784)
(128, 10)
first label of the batch 9 

iteration n: 7 execution time: 0.031780999999995174 seconds
(128, 784)
(128, 10)
first label of the batch 8 

iteration n: 8 execution time: 0.031024999999999636 seconds
(128, 784)
(128, 10)
first label of the batch 2 

iteration n: 9 execution 

#### Executing the "Graph for the datasets" for testing

In [33]:
# create an iterator
iterator = testing_dataset.make_one_shot_iterator()

# next_element
features, labels = iterator.get_next()

In [34]:
n=0

n_iter=10
with tf.Session() as sess:
    while True:
        try:
            start_time = time.clock()
            x,y = sess.run([features, labels])
            print('iteration n:', n, 'execution time:', time.clock() - start_time, 'seconds')
            print(x.shape)
            print(y.shape)
            print('first label of the batch',np.argmax(y[0]),'\n')
            n+=1
            if n>=n_iter:
                print('number of iteration reached')
                break
        except tf.errors.OutOfRangeError:
            print('tf.errors.OutOfRangeError')
            break

iteration n: 0 execution time: 3.032001000000008 seconds
(10000, 784)
(10000, 10)
first label of the batch 7 

tf.errors.OutOfRangeError


## Stored the input data as TFRecords files
TFRecord file format is a simple record-oriented binary format  
- https://medium.com/coinmonks/storage-efficient-tfrecord-for-images-6dc322b81db4
- https://www.damienpontifex.com/2017/09/18/convert-and-using-the-mnist-dataset-as-tfrecords/
- https://docs.databricks.com/_static/notebooks/horovodrunner/mnist-tensorflow-to-tfrecords.html

Contrary to numpy array or pandas dataframe this is will scale with any amount of data.

### Numpy array to TFRecords files

#### Creating the TFRecords files

In [35]:
path_test_tfrecords = 'data/mnist/tfrecords_numpy_test'
path_train_tfrecords = 'data/mnist/tfrecords_numpy_train'

In [36]:
# deleting the folder from previous try 
shutil.rmtree(path_test_tfrecords, ignore_errors=True)
shutil.rmtree(path_train_tfrecords, ignore_errors=True)

In [37]:
# creating TFRecords files for the training dataset
mnist_v1.convert_numpy_to_tfrecords(x_train, y_train, 'train', path_train_tfrecords, 1)

Processing /Users/tarrade/Desktop/Work/Data_Science/Tutorials_Codes/Python/proj_DL_models_and_pipelines_with_GCP/data/mnist/tfrecords_numpy_train/train.tfrecords data
Processing sample 60000 of 60000


In [38]:
# creating TFRecords files for the testing dataset
mnist_v1.convert_numpy_to_tfrecords(x_test, y_test, 'test', path_test_tfrecords, 1)

Processing /Users/tarrade/Desktop/Work/Data_Science/Tutorials_Codes/Python/proj_DL_models_and_pipelines_with_GCP/data/mnist/tfrecords_numpy_test/test.tfrecords data
Processing sample 10000 of 10000


#### Save TFRecord file with numpy array on GCP

In [39]:
LOCAL_DATA_TEST = path_test_tfrecords
LOCAL_DATA_TRAIN = path_train_tfrecords

In [40]:
os.environ['LOCAL_DATA_TEST'] = LOCAL_DATA_TEST
os.environ['LOCAL_DATA_TRAIN'] = LOCAL_DATA_TRAIN

In [41]:
!gsutil ls $GCS_BUCKET/mnist/

gs://ml-productive-pipeline-53122/mnist/image/
gs://ml-productive-pipeline-53122/mnist/raw/
gs://ml-productive-pipeline-53122/mnist/tfrecords/


In [42]:
!gsutil -m cp -R $LOCAL_DATA_TRAIN/ $GCS_BUCKET/mnist/tfrecords/numpy_train

Copying file://data/mnist/tfrecords_numpy_train/train.tfrecords [Content-Type=application/octet-stream]...
/ [1/1 files][ 48.2 MiB/ 48.2 MiB] 100% Done                                    
Operation completed over 1 objects/48.2 MiB.                                     


In [43]:
!gsutil -m cp -R $LOCAL_DATA_TEST/ $GCS_BUCKET/mnist/tfrecords/numpy_test

Copying file://data/mnist/tfrecords_numpy_test/test.tfrecords [Content-Type=application/octet-stream]...
| [1/1 files][  8.0 MiB/  8.0 MiB] 100% Done                                    
Operation completed over 1 objects/8.0 MiB.                                      


#### Dataset using TFRecords file to preprocess and feed data in our model 

In [44]:
training_dataset = mnist_v1.input_mnist_tfrecord_dataset_fn(glob.glob(path_train_tfrecords+'/train*.tfrecords'), 
                                                            FLAGS,
                                                            mode=tf.estimator.ModeKeys.TRAIN, 
                                                            batch_size=FLAGS.batch_size)

INFO:tensorflow:input_dataset_fn: TRAIN, train
doing training
4


In [45]:
testing_dataset = mnist_v1.input_mnist_tfrecord_dataset_fn(glob.glob(path_test_tfrecords+'/test*.tfrecords'),
                                                           FLAGS,
                                                           mode=tf.estimator.ModeKeys.EVAL, 
                                                           batch_size=len(x_test))

INFO:tensorflow:input_dataset_fn: EVAL, eval
not training 1 2
4


In [46]:
iterator = training_dataset.make_one_shot_iterator()
# next_element
features, labels = iterator.get_next()

In [47]:
n=0
n_iter=10

with tf.Session() as sess:
    while True:
        try:
            start_time = time.clock()
            x,y = sess.run([features, labels])
            print('iteration n:', n, 'execution time:', time.clock() - start_time, 'seconds')
            print(x.shape)
            print(y.shape)
            print('first label of the batch',np.argmax(y[0]),'\n')
            n+=1
            if n>=n_iter:
                print('number of iteration reached')
                break
        except tf.errors.OutOfRangeError:
            print('tf.errors.OutOfRangeError')
            break

iteration n: 0 execution time: 1.0341159999999832 seconds
(128, 784)
(128, 10)
first label of the batch 9 

iteration n: 1 execution time: 0.05230499999998983 seconds
(128, 784)
(128, 10)
first label of the batch 2 

iteration n: 2 execution time: 0.05793199999999388 seconds
(128, 784)
(128, 10)
first label of the batch 6 

iteration n: 3 execution time: 0.05706300000002784 seconds
(128, 784)
(128, 10)
first label of the batch 1 

iteration n: 4 execution time: 0.05418800000001056 seconds
(128, 784)
(128, 10)
first label of the batch 5 

iteration n: 5 execution time: 0.0534059999999954 seconds
(128, 784)
(128, 10)
first label of the batch 1 

iteration n: 6 execution time: 0.0553820000000087 seconds
(128, 784)
(128, 10)
first label of the batch 9 

iteration n: 7 execution time: 0.055336000000011154 seconds
(128, 784)
(128, 10)
first label of the batch 8 

iteration n: 8 execution time: 0.0563420000000292 seconds
(128, 784)
(128, 10)
first label of the batch 2 

iteration n: 9 executi

In [48]:
iterator = testing_dataset.make_one_shot_iterator()
# next_element
features, labels = iterator.get_next()

In [49]:
n=0

n_iter=10
with tf.Session() as sess:
    while True:
        try:
            start_time = time.clock()
            x,y = sess.run([features, labels])
            print('iteration n:', n, 'execution time:', time.clock() - start_time, 'seconds')
            print(x.shape)
            print(y.shape)
            print('first label of the batch',np.argmax(y[0]),'\n')
            n+=1
            if n>=n_iter:
                print('number of iteration reached')
                break
        except tf.errors.OutOfRangeError:
            print('tf.errors.OutOfRangeError')
            break

iteration n: 0 execution time: 3.6498189999999795 seconds
(10000, 784)
(10000, 10)
first label of the batch 7 

tf.errors.OutOfRangeError


### JPEG images to TFRecords files

#### Creating the TFRecords files

In [50]:
path_test_image_tfrecords = 'data/mnist/tfrecords_image_test'
path_train_image_tfrecords = 'data/mnist/tfrecords_image_train'

In [51]:
# deleting the folder from previous try 
shutil.rmtree(path_test_image_tfrecords, ignore_errors=True)
shutil.rmtree(path_train_image_tfrecords, ignore_errors=True)

In [1]:
# creating TFRecords files for the training dataset
mnist_v1.convert_image_to_tfrecords(glob.glob(path_train_images+'/*.jpeg'), 'train', path_train_image_tfrecords, 10)

NameError: name 'mnist_v1' is not defined

In [53]:
# creating TFRecords files for the testing dataset
mnist_v1.convert_image_to_tfrecords(glob.glob(path_test_images+'/*.jpeg'), 'test', path_test_image_tfrecords, 10)

Processing /Users/tarrade/Desktop/Work/Data_Science/Tutorials_Codes/Python/proj_DL_models_and_pipelines_with_GCP/data/mnist/tfrecords_image_test/test-1.tfrecords data
Processing sample 1000 of 1000
Processing /Users/tarrade/Desktop/Work/Data_Science/Tutorials_Codes/Python/proj_DL_models_and_pipelines_with_GCP/data/mnist/tfrecords_image_test/test-2.tfrecords data
Processing sample 1000 of 1000
Processing /Users/tarrade/Desktop/Work/Data_Science/Tutorials_Codes/Python/proj_DL_models_and_pipelines_with_GCP/data/mnist/tfrecords_image_test/test-3.tfrecords data
Processing sample 1000 of 1000
Processing /Users/tarrade/Desktop/Work/Data_Science/Tutorials_Codes/Python/proj_DL_models_and_pipelines_with_GCP/data/mnist/tfrecords_image_test/test-4.tfrecords data
Processing sample 1000 of 1000
Processing /Users/tarrade/Desktop/Work/Data_Science/Tutorials_Codes/Python/proj_DL_models_and_pipelines_with_GCP/data/mnist/tfrecords_image_test/test-5.tfrecords data
Processing sample 1000 of 1000
Processing

#### Save TFRecord file with JPEG image on GCP

In [54]:
LOCAL_DATA_TEST = path_test_image_tfrecords
LOCAL_DATA_TRAIN = path_train_image_tfrecords

In [55]:
os.environ['LOCAL_DATA_TEST'] = LOCAL_DATA_TEST
os.environ['LOCAL_DATA_TRAIN'] = LOCAL_DATA_TRAIN

In [56]:
!gsutil ls $GCS_BUCKET/mnist/

gs://ml-productive-pipeline-53122/mnist/image/
gs://ml-productive-pipeline-53122/mnist/raw/
gs://ml-productive-pipeline-53122/mnist/tfrecords/


In [59]:
!gsutil -m cp -R $LOCAL_DATA_TRAIN/ $GCS_BUCKET/mnist/tfrecords/image_train

Copying file://data/mnist/tfrecords_image_train/train-10.tfrecords [Content-Type=application/octet-stream]...
Copying file://data/mnist/tfrecords_image_train/train-6.tfrecords [Content-Type=application/octet-stream]...
Copying file://data/mnist/tfrecords_image_train/train-4.tfrecords [Content-Type=application/octet-stream]...
Copying file://data/mnist/tfrecords_image_train/train-1.tfrecords [Content-Type=application/octet-stream]...
Copying file://data/mnist/tfrecords_image_train/train-7.tfrecords [Content-Type=application/octet-stream]...
Copying file://data/mnist/tfrecords_image_train/train-9.tfrecords [Content-Type=application/octet-stream]...
Copying file://data/mnist/tfrecords_image_train/train-2.tfrecords [Content-Type=application/octet-stream]...
Copying file://data/mnist/tfrecords_image_train/train-8.tfrecords [Content-Type=application/octet-stream]...
Copying file://data/mnist/tfrecords_image_train/train-3.tfrecords [Content-Type=application/octet-stream]...
Copying file://dat

In [60]:
!gsutil -m cp -R $LOCAL_DATA_TEST/ $GCS_BUCKET/mnist/tfrecords/image_test

Copying file://data/mnist/tfrecords_image_test/test-3.tfrecords [Content-Type=application/octet-stream]...
Copying file://data/mnist/tfrecords_image_test/test-5.tfrecords [Content-Type=application/octet-stream]...
Copying file://data/mnist/tfrecords_image_test/test-8.tfrecords [Content-Type=application/octet-stream]...
Copying file://data/mnist/tfrecords_image_test/test-9.tfrecords [Content-Type=application/octet-stream]...
Copying file://data/mnist/tfrecords_image_test/test-2.tfrecords [Content-Type=application/octet-stream]...
Copying file://data/mnist/tfrecords_image_test/test-4.tfrecords [Content-Type=application/octet-stream]...
Copying file://data/mnist/tfrecords_image_test/test-7.tfrecords [Content-Type=application/octet-stream]...
Copying file://data/mnist/tfrecords_image_test/test-1.tfrecords [Content-Type=application/octet-stream]...
Copying file://data/mnist/tfrecords_image_test/test-6.tfrecords [Content-Type=application/octet-stream]...
Copying file://data/mnist/tfrecords_i

#### Dataset using TFRecords file to preprocess and feed data in our model 

In [104]:
training_dataset = mnist_v1.input_mnist_tfrecord_dataset_fn(glob.glob(path_train_image_tfrecords+'/train*.tfrecords'), 
                                                            FLAGS,
                                                            mode=tf.estimator.ModeKeys.TRAIN, 
                                                            batch_size=FLAGS.batch_size)

INFO:tensorflow:input_dataset_fn: TRAIN, train
doing training
4


In [105]:
type(training_dataset)

tensorflow.python.data.ops.dataset_ops.PrefetchDataset

In [107]:
iterator = training_dataset.make_one_shot_iterator()
print(type(iterator))
# next_element
features, labels = iterator.get_next()
print(type(features), type(labels))

<class 'tensorflow.python.data.ops.iterator_ops.Iterator'>
<class 'tensorflow.python.framework.ops.Tensor'> <class 'tensorflow.python.framework.ops.Tensor'>


In [101]:
testing_dataset = mnist_v1.input_mnist_tfrecord_dataset_fn(glob.glob(path_test_image_tfrecords+'/test*.tfrecords'),
                                                           FLAGS,
                                                           mode=tf.estimator.ModeKeys.EVAL, 
                                                           batch_size=len(x_test))

INFO:tensorflow:input_dataset_fn: EVAL, eval
not training 1 2
4


In [91]:
iterator = training_dataset.make_one_shot_iterator()
# next_element
features, labels = iterator.get_next()

In [99]:
n=0
n_iter=100000
debug=False
with tf.Session() as sess:
    while True:
        try:
            start_time = time.clock()
            x,y = sess.run([features, labels])
            if debug:
                print('iteration n:', n, 'execution time:', time.clock() - start_time, 'seconds')
                print(x.shape)
                print(y.shape)
                print('first label of the batch',np.argmax(y[0]),'\n')

            #print(n%1000)
            if ((n%100)==0):
                print(n, x.shape)
            n+=1
            if n>=n_iter:
                print('number of iteration reached')
                break
        except tf.errors.OutOfRangeError:
            print(n, x.shape)
            print('tf.errors.OutOfRangeError')
            print('total:', x.shape[0]*n, 'events')
            break

0 (128, 784)
100 (128, 784)
200 (128, 784)
300 (128, 784)
400 (128, 784)
468 (128, 784)
tf.errors.OutOfRangeError
total: 59904 events


In [102]:
iterator = testing_dataset.make_one_shot_iterator()
# next_element
features, labels = iterator.get_next()

In [103]:
n=0

n_iter=10
with tf.Session() as sess:
    while True:
        try:
            start_time = time.clock()
            x,y = sess.run([features, labels])
            print('iteration n:', n, 'execution time:', time.clock() - start_time, 'seconds')
            print(x.shape)
            print(y.shape)
            print('first label of the batch',np.argmax(y[0]),'\n')
            n+=1
            if n>=n_iter:
                print('number of iteration reached')
                break
        except tf.errors.OutOfRangeError:
            print('tf.errors.OutOfRangeError')
            print('total:', x.shape[0]*n, 'events')
            break

iteration n: 0 execution time: 3.766746000000012 seconds
(10000, 784)
(10000, 10)
first label of the batch 4 

tf.errors.OutOfRangeError
total: 10000 events
